<a href="https://colab.research.google.com/github/MesquitaALucas/2020-2-exercicio-revisao-refatoracao/blob/master/TP1_LucasMesquita.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

### **TP - 1 MACHINE LEARINING - REDES NEURAIS E BACK PROPAGATION**



---



LUCAS MESQUITA ANDRADE - 2020054668
## Requisitos

- **Rede neural de 3 camadas:**

_Função sigmóide_ como função não-linear.
Entrada: 784 unidades.
Camada oculta: <span style=color:pink>variar entre 25, 50 e 100</span>.
Camada de saída: 10 unidades (classes).

- **Loss:**

Função *cross-entropy*.

- **Conjunto de dados MNIST:**

5000 entradas, 10 possíveis classes (dígitos).
1ª coluna é o dígito (classe resposta).
28*28=784 colunas subsequentes são os valores dos pixels.

- **Algoritmos para cálculo de gradiente (quantos dados ver para calcular gradiente):**

<span style=color:pink>Comparar entre *Gradient Descent (GD)*, *Stochastic Gradient Descent (SGD)* e *Mini-Batch (10 e 50)* </span>.

- **Taxa de aprendizado:**

<span style=color:pink>Variar entre 0.5, 1 e 10</span>.

**IMPORTAÇÕES**

In [ ]:
import numpy as np
import torch
import torch.nn.functional as F
import matplotlib.pyplot as plt
from torch import nn, optim
import pandas as pd
from sklearn.model_selection import train_test_split, KFold
from sklearn.metrics import accuracy_score, f1_score
import plotly.graph_objects as go
from plotly.subplots import make_subplots


**IMPLEMENTAÇÃO DA REDE**

In [ ]:

class Modelo(nn.Module):
    def __init__(self, input=784, hl=100, output=10):
        super().__init__()
        self.fIn = nn.Linear(input, hl)
        self.fOut = nn.Linear(hl, output)

    def forward(self, aux):
        aux = torch.sigmoid(self.fIn(aux))
        aux = self.fOut(aux)
        return aux


def calcular_metricas(y_true, y_pred):
    acc = accuracy_score(y_true, y_pred)
    f1 = f1_score(y_true, y_pred, average='weighted')
    return acc, f1


def treinar_modelo(algoritmo, modelo, criterio, optimizer, X_treino, y_treino, epocas=5, batch_size=None):
    losses = []

    n = len(X_treino)

    for epoca in range(epocas):
        if algoritmo == 'GD':
            # Gradient Descent
            y_pred = modelo(X_treino)
            loss = criterio(y_pred, y_treino)
            losses.append(loss.item())

            optimizer.zero_grad()
            loss.backward()
            optimizer.step()

        elif algoritmo == 'SGD':
            # Stochastic Gradient Descent
            for i in range(n):
                X_batch = X_treino[i].unsqueeze(0)
                y_batch = y_treino[i].unsqueeze(0)

                y_pred = modelo(X_batch)
                loss = criterio(y_pred, y_batch)

                optimizer.zero_grad()
                loss.backward()
                optimizer.step()

                losses.append(loss.item())

        elif algoritmo == 'Mini-Batch':
            # Mini-Batch Gradient Descent
            for i in range(0, n, batch_size):
                X_batch = X_treino[i:i+batch_size]
                y_batch = y_treino[i:i+batch_size]

                y_pred = modelo(X_batch)
                loss = criterio(y_pred, y_batch)

                optimizer.zero_grad()
                loss.backward()
                optimizer.step()

                losses.append(loss.item())

    return losses

**DATA SET, NORMALIZAÇÃO DOS DADOS E HIPERPARAMETRO**

In [ ]:

df_dataset = pd.read_csv('data_tp1.csv', header=None)
X = df_dataset.drop(df_dataset.columns[0], axis=1).values
y = df_dataset.iloc[:, 0].values

X = X / 255.0  # Normalização dos dados

# Definição dos hiperparâmetros
hidden_units_options = [25, 50, 100]
learning_rates = [0.5, 1, 10]
epocas = 5
batch_size_mb_10 = 10
batch_size_mb_50 = 50

all_losses_gd = {}
all_accuracies_gd = {}
all_f1_scores_gd = {}
all_test_errors_gd = {}

all_losses_sgd = {}
all_accuracies_sgd = {}
all_f1_scores_sgd = {}
all_test_errors_sgd = {}

all_losses_mb_10 = {}
all_accuracies_mb_10 = {}
all_f1_scores_mb_10 = {}
all_test_errors_mb_10 = {}

all_losses_mb_50 = {}
all_accuracies_mb_50 = {}
all_f1_scores_mb_50 = {}
all_test_errors_mb_50 = {}

**FUNÇÕES PARA PLOTAGENS DOS GRÁFICOS**

In [ ]:

def criar_grafico_perda_plotly(losses, algoritmo):
    fig = go.Figure()
    for i, loss in enumerate(losses):
        fig.add_trace(go.Scatter(x=list(range(1, len(loss) + 1)), y=loss, mode='lines', name=f'Fold {i+1}'))

    fig.update_layout(title=f'Convergência da Perda - {algoritmo}',
                      xaxis_title='Época',
                      yaxis_title='Perda',
                      legend_title='Folds',
                      showlegend=True,
                      height=600,  # Definindo altura
                      width=800    # Definindo largura
                     )
    fig.show()


def plotar_metricas_plotly(metricas_dict, hiperparametro, algoritmo):
    fig = go.Figure()

    for metrica, valores in metricas_dict.items():
        for key, data in valores.items():
            fig.add_trace(go.Scatter(x=list(range(1, len(data) + 1)), y=data, mode='lines', name=f'{metrica} - {key} ({algoritmo})'))

    fig.update_layout(title=f'Métricas de Desempenho - {algoritmo} ({hiperparametro})',
                      xaxis_title='Época',
                      yaxis_title='Valor',
                      legend_title='Métricas',
                      showlegend=True,
                      height=600,  # Definindo altura
                      width=800    # Definindo largura
                     )
    fig.show()

def criar_subplots_metricas(metricas, erros_teste, titulo, algoritmo):
    fig = make_subplots(rows=1, cols=2, subplot_titles=('Métricas de Desempenho', 'Erros de Teste'))

    for metrica, valores in metricas.items():
        for key, data in valores.items():
            fig.add_trace(go.Scatter(x=list(range(1, len(data) + 1)), y=data, mode='lines', name=f'{metrica} - {key} ({algoritmo})'), row=1, col=1)

    for key, data in erros_teste.items():
        fig.add_trace(go.Scatter(x=list(range(1, len(data) + 1)), y=data, mode='lines', name=f'Erro de Teste - {key} ({algoritmo})'), row=1, col=2)

    fig.update_layout(title=titulo,
                      xaxis_title='Época',
                      yaxis_title='Valor',
                      legend_title='Métricas',
                      showlegend=True,
                      height=600,
                      width=1200
                     )
    fig.show()

**EXECUÇÃO DO TREINAMENTO COM A VARIAÇÃO DE PARAMETROS REQUISATADA**

In [ ]:
# Loop sobre as opções de unidades ocultas e taxas de aprendizado
for hidden_layer in hidden_units_options:
    for lr in learning_rates:
        losses_gd = []
        accuracies_gd = []
        f1_scores_gd = []
        test_errors_gd = []

        losses_sgd = []
        accuracies_sgd = []
        f1_scores_sgd = []
        test_errors_sgd = []

        losses_mb_10 = []
        accuracies_mb_10 = []
        f1_scores_mb_10 = []
        test_errors_mb_10 = []

        losses_mb_50 = []
        accuracies_mb_50 = []
        f1_scores_mb_50 = []
        test_errors_mb_50 = []

        kf = KFold(n_splits=5, shuffle=True, random_state=42)

        for fold, (train_index, val_index) in enumerate(kf.split(X)):
            print(f"Treinando para fold {fold + 1} - Hidden Layer: {hidden_layer}, Learning Rate: {lr}")


            modelo_gd = Modelo(hl=hidden_layer)
            criterio_gd = nn.CrossEntropyLoss()
            optimizer_gd = optim.SGD(modelo_gd.parameters(), lr=lr)

            modelo_sgd = Modelo(hl=hidden_layer)
            criterio_sgd = nn.CrossEntropyLoss()
            optimizer_sgd = optim.SGD(modelo_sgd.parameters(), lr=lr)

            modelo_mb_10 = Modelo(hl=hidden_layer)
            criterio_mb_10 = nn.CrossEntropyLoss()
            optimizer_mb_10 = optim.SGD(modelo_mb_10.parameters(), lr=lr)

            modelo_mb_50 = Modelo(hl=hidden_layer)
            criterio_mb_50 = nn.CrossEntropyLoss()
            optimizer_mb_50 = optim.SGD(modelo_mb_50.parameters(), lr=lr)

            X_train_fold = torch.FloatTensor(X[train_index])
            y_train_fold = torch.LongTensor(y[train_index])
            X_val_fold = torch.FloatTensor(X[val_index])
            y_val_fold = y[val_index]

            # Treinamento Gradient Descent
            fold_losses_gd = treinar_modelo('GD', modelo_gd, criterio_gd, optimizer_gd, X_train_fold, y_train_fold, epocas=epocas)
            losses_gd.append(fold_losses_gd)

            modelo_gd.eval()
            with torch.no_grad():
                y_pred_gd = modelo_gd(X_val_fold)
                _, predicted_gd = torch.max(y_pred_gd, 1)
                acc_gd, f1_gd = calcular_metricas(y_val_fold, predicted_gd.numpy())
                accuracies_gd.append(acc_gd)
                f1_scores_gd.append(f1_gd)

                # Calcular erro de teste
                test_error_gd = criterio_gd(y_pred_gd, torch.LongTensor(y_val_fold)).item()
                test_errors_gd.append(test_error_gd)

            # Treinamento Stochastic Gradient Descent
            fold_losses_sgd = treinar_modelo('SGD', modelo_sgd, criterio_sgd, optimizer_sgd, X_train_fold, y_train_fold, epocas=epocas)
            losses_sgd.append(fold_losses_sgd)

            modelo_sgd.eval()
            with torch.no_grad():
                y_pred_sgd = modelo_sgd(X_val_fold)
                _, predicted_sgd = torch.max(y_pred_sgd, 1)
                acc_sgd, f1_sgd = calcular_metricas(y_val_fold, predicted_sgd.numpy())
                accuracies_sgd.append(acc_sgd)
                f1_scores_sgd.append(f1_sgd)

                # Calcular erro de teste
                test_error_sgd = criterio_sgd(y_pred_sgd, torch.LongTensor(y_val_fold)).item()
                test_errors_sgd.append(test_error_sgd)

            # Treinamento Mini-Batch Gradient Descent (batch size 10)
            fold_losses_mb_10 = treinar_modelo('Mini-Batch', modelo_mb_10, criterio_mb_10, optimizer_mb_10, X_train_fold, y_train_fold, epocas=epocas, batch_size=batch_size_mb_10)
            losses_mb_10.append(fold_losses_mb_10)

            modelo_mb_10.eval()
            with torch.no_grad():
                y_pred_mb_10 = modelo_mb_10(X_val_fold)
                _, predicted_mb_10 = torch.max(y_pred_mb_10, 1)
                acc_mb_10, f1_mb_10 = calcular_metricas(y_val_fold, predicted_mb_10.numpy())
                accuracies_mb_10.append(acc_mb_10)
                f1_scores_mb_10.append(f1_mb_10)

                # Calcular erro de teste
                test_error_mb_10 = criterio_mb_10(y_pred_mb_10, torch.LongTensor(y_val_fold)).item()
                test_errors_mb_10.append(test_error_mb_10)

            # Treinamento Mini-Batch Gradient Descent (batch size 50)
            fold_losses_mb_50 = treinar_modelo('Mini-Batch', modelo_mb_50, criterio_mb_50, optimizer_mb_50, X_train_fold, y_train_fold, epocas=epocas, batch_size=batch_size_mb_50)
            losses_mb_50.append(fold_losses_mb_50)

            modelo_mb_50.eval()
            with torch.no_grad():
                y_pred_mb_50 = modelo_mb_50(X_val_fold)
                _, predicted_mb_50 = torch.max(y_pred_mb_50, 1)
                acc_mb_50, f1_mb_50 = calcular_metricas(y_val_fold, predicted_mb_50.numpy())
                accuracies_mb_50.append(acc_mb_50)
                f1_scores_mb_50.append(f1_mb_50)

                # Calcular erro de teste
                test_error_mb_50 = criterio_mb_50(y_pred_mb_50, torch.LongTensor(y_val_fold)).item()
                test_errors_mb_50.append(test_error_mb_50)

        # Armazenando Gradient Descent
        all_losses_gd[f'{hidden_layer}_units_{lr}_lr'] = losses_gd
        all_accuracies_gd[f'{hidden_layer}_units_{lr}_lr'] = accuracies_gd
        all_f1_scores_gd[f'{hidden_layer}_units_{lr}_lr'] = f1_scores_gd
        all_test_errors_gd[f'{hidden_layer}_units_{lr}_lr'] = test_errors_gd

        # Armazenando Stochastic Gradient Descent
        all_losses_sgd[f'{hidden_layer}_units_{lr}_lr'] = losses_sgd
        all_accuracies_sgd[f'{hidden_layer}_units_{lr}_lr'] = accuracies_sgd
        all_f1_scores_sgd[f'{hidden_layer}_units_{lr}_lr'] = f1_scores_sgd
        all_test_errors_sgd[f'{hidden_layer}_units_{lr}_lr'] = test_errors_sgd

        # Armazenando Mini-Batch Gradient Descent (batch size 10)
        all_losses_mb_10[f'{hidden_layer}_units_{lr}_lr'] = losses_mb_10
        all_accuracies_mb_10[f'{hidden_layer}_units_{lr}_lr'] = accuracies_mb_10
        all_f1_scores_mb_10[f'{hidden_layer}_units_{lr}_lr'] = f1_scores_mb_10
        all_test_errors_mb_10[f'{hidden_layer}_units_{lr}_lr'] = test_errors_mb_10

        # Armazenando Mini-Batch Gradient Descent (batch size 50)
        all_losses_mb_50[f'{hidden_layer}_units_{lr}_lr'] = losses_mb_50
        all_accuracies_mb_50[f'{hidden_layer}_units_{lr}_lr'] = accuracies_mb_50
        all_f1_scores_mb_50[f'{hidden_layer}_units_{lr}_lr'] = f1_scores_mb_50
        all_test_errors_mb_50[f'{hidden_layer}_units_{lr}_lr'] = test_errors_mb_50

Treinando para fold 1 - Hidden Layer: 25, Learning Rate: 0.5
Treinando para fold 2 - Hidden Layer: 25, Learning Rate: 0.5
Treinando para fold 3 - Hidden Layer: 25, Learning Rate: 0.5
Treinando para fold 4 - Hidden Layer: 25, Learning Rate: 0.5
Treinando para fold 5 - Hidden Layer: 25, Learning Rate: 0.5
Treinando para fold 1 - Hidden Layer: 25, Learning Rate: 1
Treinando para fold 2 - Hidden Layer: 25, Learning Rate: 1
Treinando para fold 3 - Hidden Layer: 25, Learning Rate: 1
Treinando para fold 4 - Hidden Layer: 25, Learning Rate: 1
Treinando para fold 5 - Hidden Layer: 25, Learning Rate: 1
Treinando para fold 1 - Hidden Layer: 25, Learning Rate: 10
Treinando para fold 2 - Hidden Layer: 25, Learning Rate: 10
Treinando para fold 3 - Hidden Layer: 25, Learning Rate: 10
Treinando para fold 4 - Hidden Layer: 25, Learning Rate: 10
Treinando para fold 5 - Hidden Layer: 25, Learning Rate: 10
Treinando para fold 1 - Hidden Layer: 50, Learning Rate: 0.5
Treinando para fold 2 - Hidden Layer: 5

**CRIAÇÃO DOS GRÁFICOS DE CONVERGÊNCIA DE ERRO:**

Para facilitar a vizualização o entendimento e ao mesmo tempo diminuir o número de vizualizações, está sendo feito a plotagem da perda média considerando épocas e folds para todos os cenários. Os titúlos especificam qual gráfico refernecia cada combinação de algoritmo, número de componentes na hidden layer e taxa de aprendizado


In [ ]:
import numpy as np
import plotly.graph_objects as go
from plotly.subplots import make_subplots

# Função para criar subplots de convergência da perda com destaque para a média
def criar_subplots_convergencia_perda(losses_dict, algoritmo):
    rows = len(hidden_units_options)  # Número de linhas = número de configurações de unidades ocultas
    cols = len(learning_rates)  # Número de colunas = número de taxas de aprendizado

    fig = make_subplots(
        rows=rows,
        cols=cols,
        subplot_titles=[
            f"{hidden_layer} hidden units, {lr} lr"
            for hidden_layer in hidden_units_options
            for lr in learning_rates
        ]
    )

    for i, hidden_layer in enumerate(hidden_units_options):
        for j, lr in enumerate(learning_rates):
            key = f'{hidden_layer}_units_{lr}_lr'
            losses = losses_dict[key]

            mean_losses = np.mean(losses, axis=0)
            std_losses = np.std(losses, axis=0)

            # Plotting mean loss without standard deviation as error bars
            fig.add_trace(
                go.Scatter(
                    x=list(range(1, len(mean_losses) + 1)),
                    y=mean_losses,
                    mode='lines+markers',
                    line=dict(color='blue', width=2),  # Linha da média mais espessa e em azul
                    marker=dict(size=6),
                    name=f'{algoritmo} - Média',
                    showlegend=False
                ),
                row=i+1, col=j+1
            )

    fig.update_layout(
        height=300*rows,
        width=400*cols,
        title_text=f'Convergência da Perda - {algoritmo}',
        showlegend=False
    )

    fig.show()

# Chamar a função para cada algoritmo
criar_subplots_convergencia_perda(all_losses_gd, 'Gradient Descent')
criar_subplots_convergencia_perda(all_losses_sgd, 'Stochastic Gradient Descent')
criar_subplots_convergencia_perda(all_losses_mb_10, f'Mini-Batch Gradient Descent (batch size {batch_size_mb_10})')
criar_subplots_convergencia_perda(all_losses_mb_50, f'Mini-Batch Gradient Descent (batch size {batch_size_mb_50})')


Para o GD: É possível perceber que ele tem melhor desempenho para LR de 1, sendo o minimo atingido com 25 hidden units, o mínimo sendo cerca de 2,21. Além disso, para lr = 10 vemos um comportamento que demonstra instabilidade, e que nãop parecem ajudar na convergência do modelo. Pouca diferença foi observada entre 25 e 50 hiden units, mas houve uma grande diferença quando comparado ao de 100, sugerindo que mais nós podem ser pior para o processo

PARA SGD: Percebe-se primeiramente que na leraning rate de 10 temos as maiores escalas de erro, superanto em até 10x as das outras duas possibilidades em todas as váricções de hidden units, o que sugere uma falaha na hora de aprender uma boa modelagem de dados. Aqui a LR = 0.5 parece ser a melhor escolha, ela é a que a escala de erro foi a menor para todas as possibilidades de hidden lares, sugerindo que para o caso estudado atualizações de pesos mais sutis podem Adquirir resultados melhores do pontio de vista de learning rates. Ademais, não foi possível perceber nenhuma grande mudança em relação a variação de hidden units.

Para os Mini Batch10: Vemos uma repeticção do comportamento em que a menor esclaa de erro é a de lr = 0.5, tambem indicando atualizações mais conservadoras podem ter melhores. Contudo, o erro está muito baixo, o que sugere a possibilidade de um overfitting neste caso. Além disso, quanto mais nós, menor o erro nesse caso sugerindo que o processamento em níos demais tambem pode implicar no overfitting

Para os Mini Batch50: A convergência desse minibatch foi muito similar a do outro minibatch, seguindo todos os padrões citados anteriormente, convergindo ainda melhor o erro, que em seu melhor caso chego a 0,1. Ou seja, sugere overfitting, e quanto a menor a learning rate melhor e quanto mais nós melhor.

Numa comparação geral: Nenhum algoritmo se sobresaiu bem com a learning rate muito alta, implicando que o problema requer uma learning rate mais baixa para todos os casos. Além disso, o número de nós, generalizando, quanto mais melhores foram os resultados. Tivemos alguns indicios de Overfitting mas nenhum de Underfitting.


**CRIAÇÃO DOS GRÁFICOS DE MÉTRICAS DE DESEMPENHO**:

In [ ]:
# Preparando dados para plotar métricas de desempenho
all_accuracies = {
    'Gradient Descent': all_accuracies_gd,
    'Stochastic Gradient Descent': all_accuracies_sgd,
    f'Mini-Batch Gradient Descent (batch size {batch_size_mb_10})': all_accuracies_mb_10,
    f'Mini-Batch Gradient Descent (batch size {batch_size_mb_50})': all_accuracies_mb_50
}

all_f1_scores = {
    'Gradient Descent': all_f1_scores_gd,
    'Stochastic Gradient Descent': all_f1_scores_sgd,
    f'Mini-Batch Gradient Descent (batch size {batch_size_mb_10})': all_f1_scores_mb_10,
    f'Mini-Batch Gradient Descent (batch size {batch_size_mb_50})': all_f1_scores_mb_50
}

all_test_errors = {
    'Gradient Descent': all_test_errors_gd,
    'Stochastic Gradient Descent': all_test_errors_sgd,
    f'Mini-Batch Gradient Descent (batch size {batch_size_mb_10})': all_test_errors_mb_10,
    f'Mini-Batch Gradient Descent (batch size {batch_size_mb_50})': all_test_errors_mb_50
}

for algoritmo in all_accuracies.keys():
    metricas_acuracia = all_accuracies[algoritmo]
    metricas_f1_score = all_f1_scores[algoritmo]
    metricas_test_error = all_test_errors[algoritmo]

    metricas = {
        'Acurácia': metricas_acuracia,
        'F1 Score': metricas_f1_score
    }
    criar_subplots_metricas(metricas, metricas_test_error, f'Métricas de Desempenho e Erros de Teste - {algoritmo}', algoritmo)


GD: É possível ver o menor erro de teste com 25 hidden units e 10 hidden layers, e que é onde sua melhor acuracia tambem, o que contradiz um pouco as conclusões tiradas anteriormente.

SGD: O sgd teve melhor acuracia no caso em que os dois fatores foram minizados, indicando que é melhor que as alterações de pesos sejam mais conservadores. O erro de teste é minimzado em 25 hd e lr -= 10

MiniBatch: AMbos minibatchs tiveram comportamentos muito similares. Todas as acuracias tiveram resultadaos muito proximos, toodos entorno de 0,89 um resultado extremamente muito bom, indicando bom rendimento de todas, além de que o erro de teste é maior quando temos menos hidden units, indicando que maiss hidden units é de melhor resultado